In [1]:
!pip install transformers accelerate bitsandbytes sentencepiece einops

In [ ]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel

MODEL_ID = "AIBunCho/japanese-novel-gpt-j-6b"
MODEL_QLORA_ID = "tsukemono/japanese-novel-gpt-j-6b-qlora-marisa"

In [ ]:
# tokenizer設定
tokenizer = AutoTokenizer.from_pretrained(
    MODEL_ID,
    use_fast=True,
)
ret_token = tokenizer("[SEP]",  truncation=True, add_special_tokens=False)['input_ids'][-1]
bra_token = tokenizer("（",  truncation=True, add_special_tokens=False)['input_ids'][-1]

In [3]:
# model設定
model = AutoModelForCausalLM.from_pretrained(MODEL_ID, device_map="auto", load_in_8bit=True, torch_dtype=torch.float16)
model.eval()
model = PeftModel.from_pretrained(model, MODEL_QLORA_ID, device_map="auto")

Loading checkpoint shards: 100%|██████████| 2/2 [00:24<00:00, 12.18s/it]


In [4]:
# テキスト生成関数の定義
def generate(text,maxTokens=512):
    prompt = f"ユーザー: {text}[SEP]魔理沙: "
    input_ids = tokenizer(prompt,
        return_tensors="pt",
        truncation=True,
        add_special_tokens=False
    ).input_ids.cuda()
    with torch.no_grad():
        outputs = model.generate(
            input_ids = input_ids,
            max_length=maxTokens,
            do_sample=True,
            temperature=0.1,
            top_p=0.9,
            top_k=20,
            no_repeat_ngram_size=2,
            repetition_penalty=1.15,
            pad_token_id=tokenizer.pad_token_id,
            bad_words_ids=[[bra_token]],
            eos_token_id = [tokenizer.eos_token_id,ret_token]
        )
    outputs = tokenizer.decode(outputs.tolist()[0][input_ids.size(1):],skip_special_tokens=True)
    return outputs

In [5]:
generate("強さの秘訣はなんですか?")

'努力と根性だ! '

In [6]:
generate("ブッダの思想についてどう思う?")

'良いんじゃないか。私は好きだぜ、この考え方は。ただ、ちょっと極端すぎる気もするけどな。 '

In [7]:
generate("日本で一番高い山は?")

'富士山だ! '

In [8]:
generate("幻想郷ってどんな場所?")

'そうだな。一言で言えば「忘れられた者の楽園」だな。 '